In [1]:
import numpy as np
from collections import Counter
import tensorflow as tf
from keras.callbacks import ModelCheckpoint
from keras.models import Sequential
from keras.layers.core import Dense, Activation, Dropout
from keras.layers.recurrent import LSTM

Using TensorFlow backend.


# Reading Corpus

In [2]:
corpus_file = open('corpus.txt', mode='r')
corpus = corpus_file.read()
# corpus = corpus.lower()
print(corpus[:45])

From even the greatest of horrors irony is se


In [3]:
vocab = set(corpus)
num_classes = len(vocab)
print(vocab)
print(num_classes)

vocab_to_int = {c:i for i, c in enumerate(vocab)}
int_to_vocab = {i:c for i, c in enumerate(vocab)}

encoded = [vocab_to_int[c] for c in corpus]
textsize = len(encoded)
print(encoded[:45])
print(textsize)

{'_', '8', 'l', 'R', 'e', ';', '-', '0', 'H', ']', ',', 'g', 'x', 'U', 'j', 'u', 'L', 'n', '1', '3', 'W', 'k', 't', "'", 'f', 'D', '&', '.', ' ', 'p', '!', 'C', '7', 'N', 'V', 'Z', '2', '?', '[', 'K', 'B', 'o', 'J', 'i', 'd', 'M', 'a', 'b', 'w', 'Y', 'G', 'c', 'v', 'A', '6', '"', 's', 'P', 'S', ':', 'z', 'r', 'I', 'T', 'q', '4', 'y', '5', '*', 'E', 'O', 'F', 'm', '9', 'h'}
75
[71, 61, 41, 72, 28, 4, 52, 4, 17, 28, 22, 74, 4, 28, 11, 61, 4, 46, 22, 4, 56, 22, 28, 41, 24, 28, 74, 41, 61, 61, 41, 61, 56, 28, 43, 61, 41, 17, 66, 28, 43, 56, 28, 56, 4]
62936


In [5]:
# Hyperparams
# samples = 1300
steps = 100
dropout = 0.2
epochs = 50
batch_size = 64



In [6]:
X = []
y = []

for i in range(0, textsize - steps, 1):
    X.append(encoded[i : i + steps])
    y.append(encoded[i + steps])

X = np.reshape(X, (len(X), steps, 1))
X = X/float(num_classes)

X_train = X
y_train = np.eye(num_classes)[y]

print(X_train.shape)
print(y_train.shape)


(62836, 100, 1)
(62836, 75)


In [7]:
Counter(y)
# print(X[1,:,:])

Counter({0: 26,
         1: 24,
         2: 2071,
         3: 38,
         4: 6264,
         5: 85,
         6: 263,
         7: 5,
         8: 68,
         9: 1,
         10: 650,
         11: 971,
         12: 92,
         13: 4,
         14: 26,
         15: 1440,
         16: 9,
         17: 3619,
         18: 55,
         19: 5,
         20: 55,
         21: 276,
         22: 4454,
         23: 47,
         24: 1214,
         25: 23,
         26: 1,
         27: 342,
         28: 11038,
         29: 827,
         30: 1,
         31: 29,
         32: 30,
         33: 22,
         34: 1,
         35: 2,
         36: 12,
         37: 4,
         38: 1,
         39: 1,
         40: 39,
         41: 3563,
         42: 12,
         43: 3274,
         44: 2353,
         45: 39,
         46: 3983,
         47: 686,
         48: 1035,
         49: 2,
         50: 16,
         51: 1429,
         52: 472,
         53: 54,
         54: 20,
         55: 12,
         56: 3039,
         57: 32,


In [8]:
model = Sequential()
model.add(LSTM(256,input_shape=(X_train.shape[1], X_train.shape[2]),return_sequences=True))
model.add(Dropout(dropout))
model.add(LSTM(256))
model.add(Dropout(dropout))
model.add(Dense(num_classes, activation='softmax'))
model.compile(loss="categorical_crossentropy", optimizer="adam")

In [9]:
filepath="weights-improvement-{epoch:02d}-{loss:.4f}.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='loss', verbose=1, save_best_only=True, mode='min')
callbacks_list = [checkpoint]

In [10]:
model.fit(X_train, y_train, batch_size = batch_size, epochs=epochs, callbacks=callbacks_list)

Epoch 1/50
62836/62836 [==============================] - 277s - loss: 3.0259   
Epoch 2/50
62836/62836 [==============================] - 269s - loss: 2.8412   
Epoch 3/50
62836/62836 [==============================] - 270s - loss: 2.5858   
Epoch 4/50
62836/62836 [==============================] - 271s - loss: 2.4622   
Epoch 5/50
62836/62836 [==============================] - 272s - loss: 2.3804   
Epoch 6/50
62836/62836 [==============================] - 273s - loss: 2.3183   
Epoch 7/50
62836/62836 [==============================] - 273s - loss: 2.2619   
Epoch 8/50
62836/62836 [==============================] - 276s - loss: 2.2100   
Epoch 9/50
62836/62836 [==============================] - 277s - loss: 2.1598   
Epoch 10/50
62836/62836 [==============================] - 275s - loss: 2.1186   
Epoch 11/50
62836/62836 [==============================] - 277s - loss: 2.0696   
Epoch 12/50
62836/62836 [==============================] - 275s - loss: 2.0301   
Epoch 13/50
62836/62836 [

In [11]:
y_pred = model.predict(np.reshape(X_train[102,:,:],(1,steps,1)))
print(y_pred)
y_transformed = np.argmax(y_pred)
print(y_transformed)
print(int_to_vocab[y_transformed])

[[  3.87497857e-06   1.08972245e-05   9.40865930e-03   4.75523155e-03
    2.50513181e-02   1.75368385e-07   1.00958996e-05   8.65565468e-08
    1.84051212e-04   2.51315857e-10   8.75905982e-07   3.44021525e-03
    5.39428802e-05   1.99379400e-07   3.51993708e-06   2.61816904e-02
    4.99261614e-06   2.52217166e-02   1.88818420e-04   4.56473686e-07
    1.49845134e-03   1.07249757e-03   7.95291215e-02   1.27279762e-07
    1.47723451e-01   1.14402785e-04   4.10668388e-10   3.26746999e-07
    4.55783338e-05   2.73491830e-01   6.16480716e-13   2.63324962e-03
    6.14643659e-06   6.69569781e-05   3.80742382e-11   1.61086078e-08
    1.30649141e-05   2.28279479e-10   6.23320883e-12   2.25205166e-09
    3.91243475e-06   1.23833781e-02   2.66633424e-06   4.30159643e-02
    8.34635645e-02   2.54331335e-05   2.74780821e-02   5.13028260e-03
    3.03466688e-03   2.49739252e-08   1.18906930e-04   5.51047139e-02
    3.42055247e-03   1.65016809e-03   2.44047005e-05   3.30472039e-06
    8.12624991e-02  

In [12]:
seed = np.random.randint(textsize-steps)
x_seed = corpus[seed:seed + steps]
x_seed = [vocab_to_int[char] for char in x_seed]
x_seed = np.reshape(x_seed, (1, steps, 1))
x_seed = x_seed/float(num_classes)
print(x_seed)

[[[ 0.22666667]
  [ 0.2       ]
  [ 0.81333333]
  [ 0.74666667]
  [ 0.05333333]
  [ 0.13333333]
  [ 0.37333333]
  [ 0.29333333]
  [ 0.98666667]
  [ 0.05333333]
  [ 0.37333333]
  [ 0.61333333]
  [ 0.22666667]
  [ 0.68      ]
  [ 0.57333333]
  [ 0.05333333]
  [ 0.22666667]
  [ 0.29333333]
  [ 0.37333333]
  [ 0.6       ]
  [ 0.61333333]
  [ 0.81333333]
  [ 0.57333333]
  [ 0.61333333]
  [ 0.37333333]
  [ 0.04      ]
  [ 0.54666667]
  [ 0.62666667]
  [ 0.62666667]
  [ 0.57333333]
  [ 0.22666667]
  [ 0.74666667]
  [ 0.13333333]
  [ 0.37333333]
  [ 0.74666667]
  [ 0.05333333]
  [ 0.05333333]
  [ 0.96      ]
  [ 0.05333333]
  [ 0.58666667]
  [ 0.37333333]
  [ 0.58666667]
  [ 0.61333333]
  [ 0.81333333]
  [ 0.28      ]
  [ 0.02666667]
  [ 0.88      ]
  [ 0.37333333]
  [ 0.61333333]
  [ 0.64      ]
  [ 0.61333333]
  [ 0.81333333]
  [ 0.05333333]
  [ 0.37333333]
  [ 0.54666667]
  [ 0.32      ]
  [ 0.37333333]
  [ 0.74666667]
  [ 0.54666667]
  [ 0.96      ]
  [ 0.05333333]
  [ 0.29333333]
  [ 0.98

In [13]:
x = x_seed
out = []
charsize = 500

for i in range(charsize):
    y_pred = model.predict(x)
    y_transformed = np.argmax(y_pred)
    output = int_to_vocab[y_transformed]
    out.append(output)
    x_new = y_transformed/float(num_classes)
    x = np.append(x[:,1:100,:], np.reshape(x_new, (1,1,1)), axis = 1)

print('completed')

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [14]:
print(len(out))
print(''.join(out))

500
s of the hole, which was ant if the commenced to my uncle sa eritt Mud servint was senter s ranght that the family of Roueet had been servant were not on the forst hore and the necs of dnctonctitions and the family  And an an onteres. In the same simetimes sharply and peace, and the butils of nroun could seemed to be under Cartured an the Ptreet  Iowed an an evil inflane when the dark in 1763, and Havey and decirted the place. Tt was the both the dark in 1763. Harris was a partich  The house was
